In [ ]:
%pip install zstandard

In [1]:
import pandas as pd
import numpy as np
import requests
from pathlib import Path
from plotly.subplots import make_subplots
import plotly.graph_objs as go
from zstandard import ZstdDecompressor
import tensorflow as tf
from sklearn.preprocessing import MinMaxScaler

2023-03-12 13:55:03.439499: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-03-12 13:55:03.653130: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-03-12 13:55:03.653161: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2023-03-12 13:55:04.436204: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-

In [3]:
# Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')
# Create a working folder and cd to it.
!mkdir -p "/content/drive/MyDrive/Courses/EIE/Year 4/FYP"
%cd "/content/drive/MyDrive/Courses/EIE/Year 4/FYP"

Mounted at /content/drive
/content/drive/MyDrive/Courses/EIE/Year 4/FYP


In [4]:
DATASET_FILE_PATH = 'hk_opendata_journey_data.csv'
if not Path(DATASET_FILE_PATH).exists():
  print(f'Downloading hk_opendata_journey_data.csv.zst')
  r = requests.get('https://files.nekoul.com/pub/hk_opendata_journey_data.csv.zst')
  if not r.ok:
    print('Unable to download the datasets')
    exit(128)

  with open(DATASET_FILE_PATH, 'wb+') as f:
    print(f'Decompressing {DATASET_FILE_PATH}')
    dctx = ZstdDecompressor()
    decompressor = dctx.stream_writer(f)
    decompressor.write(r.content)
    print(f'Decompression done')

In [5]:
!ls -al

total 98620
-rw------- 1 root root 99897041 Dec 18 11:35 hk_opendata_journey_data.csv
drwx------ 2 root root     4096 Dec 18 14:03 model
-rw------- 1 root root  1084663 Mar 12 05:04 Traffic_time_series_forescasting.ipynb


In [6]:
df = pd.read_csv(DATASET_FILE_PATH)
feature_keys = [
  'H1-CH', 'H1-EH', 'H11-CH', 'H11-EH', 'H2-CH', 'H2-EH', 'H2-WH', 'H3-CH', 'H3-WH', 'H4-CH', 'H4-EH', 'H4-WH',
  'H5-CH', 'H5-EH', 'H5-WH', 'K01-CH', 'K01-WH', 'K02-CH', 'K02-EH', 'K03-CH', 'K03-EH', 'K03-WH', 'K04-CH', 'K04-WH',
  'K05-CH', 'K05-EH', 'K06-CH', 'K06-WH'
]

In [7]:
def plot(data, title: str = '', *,
         xaxis_title='Time', yaxis_title='Journey time', rows=1, cols=1,
         subplot_titles: list = None, subplot_pos: list = None, index: list = None):
  fig = make_subplots(rows=rows, cols=cols, subplot_titles=subplot_titles)
  for idx, s in enumerate(data):
    pos = subplot_pos[idx] if subplot_pos is not None else idx
    fig.add_trace(
      go.Scatter(x=s.index, y=s),
      row=pos // rows + 1,
      col=pos % cols + 1,
    )

  fig.update_layout(
    title={
      'text': title,
      'x': 0.5,
    },
    xaxis_title=xaxis_title,
    yaxis_title=yaxis_title,
  )
  fig.show()

In [8]:
df.index = pd.to_datetime(df['timestamp'])
# df.drop('timestamp', axis=1, inplace=True)
df_resmapled = df.resample('5Min').interpolate(method='time').iloc[1:]
df_resmapled

timestamp  H1-CH  H1-EH  H11-CH  H11-EH  H2-CH  \
timestamp                                                                       
2021-10-01 00:00:00  2021-10-01T00:00:00   -1.0   -1.0    -1.0    -1.0   -1.0   
2021-10-01 00:05:00  2021-10-01T00:05:00   -1.0   -1.0    -1.0    -1.0   -1.0   
2021-10-01 00:10:00  2021-10-01T00:10:00   -1.0   -1.0    -1.0    -1.0   -1.0   
2021-10-01 00:15:00  2021-10-01T00:15:00   -1.0   -1.0    -1.0    -1.0   -1.0   
2021-10-01 00:20:00  2021-10-01T00:20:00   -1.0   -1.0    -1.0    -1.0   -1.0   
...                                  ...    ...    ...     ...     ...    ...   
2022-11-10 23:35:00  2022-11-10T23:35:00    5.0    8.0    10.0     4.0    7.0   
2022-11-10 23:40:00  2022-11-10T23:40:00    5.0    8.0    10.0     4.0    5.0   
2022-11-10 23:45:00  2022-11-10T23:45:00    5.0    8.0    10.0     4.0    6.0   
2022-11-10 23:50:00  2022-11-10T23:50:00    5.0    8.0     9.0     4.0    5.0   
2022-11-10 23:55:00  2022-11-10T23:55:00    5.0    8.0     9.0     4.0    7.0   

                     H2-EH  H2-WH  H3-CH  H3-WH  ...  SJ2-TSCA  SJ3-LRT  \
timestamp                                        ...                      
2021-10-01 00:00:00   -1.0   -1.0   -1.0   -1.0  ...      -1.0     -1.0   
2021-10-01 00:05:00   -1.0   -1.0   -1.0   -1.0  ...      -1.0     -1.0   
2021-10-01 00:10:00   -1.0   -1.0   -1.0   -1.0  ...      -1.0     -1.0   
2021-10-01 00:15:00   -1.0   -1.0   -1.0   -1.0  ...      -1.0     -1.0   
2021-10-01 00:20:00   -1.0   -1.0   -1.0   -1.0  ...      -1.0     -1.0   
...                    ...    ...    ...    ...  ...       ...      ...   
2022-11-10 23:35:00    9.0    8.0    7.0    8.0  ...      12.0     13.0   
2022-11-10 23:40:00    9.0    8.0    7.0    8.0  ...      12.0     13.0   
2022-11-10 23:45:00    9.0    8.0    7.0    8.0  ...      12.0     12.0   
2022-11-10 23:50:00    9.0    8.0    7.0    8.0  ...      13.0     12.0   
2022-11-10 23:55:00    9.0    8.0    7.0    8.0  ...      12.0     12.0   

                     SJ3-TCT  SJ3-TSCA  SJ4-ATL  SJ4-TKTL  SJ4-TKTM  \
timestamp                                                             
2021-10-01 00:00:00     -1.0      -1.0     26.0      -1.0      -1.0   
2021-10-01 00:05:00     -1.0      -1.0     27.0      -1.0      -1.0   
2021-10-01 00:10:00     -1.0      -1.0     26.0      -1.0      -1.0   
2021-10-01 00:15:00     -1.0      -1.0     26.0      -1.0      -1.0   
2021-10-01 00:20:00     -1.0      -1.0     27.0      -1.0      -1.0   
...                      ...       ...      ...       ...       ...   
2022-11-10 23:35:00     11.0      12.0     25.0      10.0      24.0   
2022-11-10 23:40:00     11.0      12.0     27.0      12.0      23.0   
2022-11-10 23:45:00     11.0      12.0     28.0      12.0      24.0   
2022-11-10 23:50:00     10.0      12.0     27.0      12.0      23.0   
2022-11-10 23:55:00     11.0      11.0     27.0      11.0      24.0   

                     SJ4-TMCLK  SJ5-TWCP  SJ5-TWTM  
timestamp                                           
2021-10-01 00:00:00       27.0      -1.0      -1.0  
2021-10-01 00:05:00       28.0      -1.0      -1.0  
2021-10-01 00:10:00       28.0      -1.0      -1.0  
2021-10-01 00:15:00       27.0      -1.0      -1.0  
2021-10-01 00:20:00       26.0      -1.0      -1.0  
...                        ...       ...       ...  
2022-11-10 23:35:00       27.0      25.0      16.0  
2022-11-10 23:40:00       26.0      25.0      17.0  
2022-11-10 23:45:00       27.0      25.0      17.0  
2022-11-10 23:50:00       26.0      26.0      16.0  
2022-11-10 23:55:00       27.0      26.0      17.0  

[116928 rows x 65 columns]

Traceback (most recent call last):
  File "/usr/local/lib/python3.9/dist-packages/google/colab/data_table.py", line 187, in _repr_mimebundle_
    dataframe = self._preprocess_dataframe()
  File "/usr/local/lib/python3.9/dist-packages/google/colab/data_table.py", line 175, in _preprocess_dataframe
    dataframe = dataframe.reset_index()
  File "/usr/local/lib/python3.9/dist-packages/pandas/util/_decorators.py", line 311, in wrapper
    return func(*args, **kwargs)
  File "/usr/local/lib/python3.9/dist-packages/pandas/core/frame.py", line 5799, in reset_index
    new_obj.insert(0, name, level_values)
  File "/usr/local/lib/python3.9/dist-packages/pandas/core/frame.py", line 4414, in insert
    raise ValueError(f"cannot insert {column}, already exists")
ValueError: cannot insert timestamp, already exists
Traceback (most recent call last):
  File "/usr/local/lib/python3.9/dist-packages/google/colab/data_table.py", line 199, in _repr_javascript_module_
    return self._gen_js(self._preproce

In [9]:
df_resmapled.shape

(116928, 65)

In [21]:
cht = df_resmapled[['K02-CH']]
timestamp = pd.to_datetime(df_resmapled['timestamp'])
# Filter invalid time
cht = cht[cht['K02-CH'] != -1].iloc[5:]
cht['week_day'] = timestamp.dt.dayofweek
cht['hour'] = timestamp.dt.hour
cht['minute'] = timestamp.dt.minute
print(f'K02-CH shape={cht.shape}')

KeyError: ignored

In [ ]:
# Resample the datasets to 5/10/30 Min
# cht_5m = cht.resample('5Min').interpolate(method='time')
# print(f'K02-CH (5-Min) shape={cht_5m.shape}')
# cht_10m = cht.resample('10Min').interpolate(method='time')
# print(f'K02-CH (10-Min) shape={cht_10m.shape}')
# cht_30m = cht.resample('30Min').interpolate(method='time')
# print(f'K02-CH (30-Min) shape={cht_30m.shape}')

K02-CH (5-Min) shape=(102774,)
K02-CH (10-Min) shape=(51387,)
K02-CH (30-Min) shape=(17129,)


In [18]:
# plot([
#   cht,
#   cht_5m,
#   cht_10m,
#   cht_30m,
# ], 'K02-CH', rows=2, cols=2, subplot_titles=['1 Min', '5 Min', '10 Min', '30 Min'])
plot([cht['K02-CH']])

In [ ]:
def splint_and_normalize_dataset(data, *,
                                 train_ratio=0.7, val_ratio=0.2) -> (pd.Series, pd.Series, pd.Series):
  data_n = data.shape[0]
  train_n = int(data_n * train_ratio)
  val_n = int(data_n * val_ratio)

  train_data: pd.Series = data.iloc[:train_n]
  # Normalize data
  mean = train_data.mean()
  std = train_data.std()
  train_data = (train_data - mean) / std
  val_data = (data.iloc[train_n:train_n + val_n] - mean) / std
  test_data = (data.iloc[train_n + val_n:] - mean) / std
  return train_data, val_data, test_data

In [19]:
# train, val, test = splint_and_normalize_dataset(cht_5m)
data_n = cht.shape[0]
train_n = int(data_n * 0.7)
val_n = int(data_n * 0.2)

mm = MinMaxScaler(feature_range=(0, 0))
mean = cht['K02-CH'].mean()
std = cht['K02-CH'].std()
train_data = cht.iloc[:train_n]
train_data.loc[:,'K02-CH'] = (train_data['K02-CH'] - mean) / std
val_data = cht.iloc[train_n:train_n + val_n]
val_data.loc[:,'K02-CH'] = (val_data['K02-CH'] - mean) / std
test_data = cht.iloc[train_n + val_n:]
test_data.loc[:,'K02-CH'] = (test_data['K02-CH'] - mean) / std

print(f'Train data shape={train_data.shape}')
print(f'Validation data shape={val_data.shape}')
print(f'Test data shape={test_data.shape}')
plot([train_data['K02-CH'], val_data['K02-CH'], test_data['K02-CH']], 'K02-CH', rows=1, cols=1,
     subplot_titles=['Train', 'Validation', 'Test'], subplot_pos=[0, 0, 0])

/usr/local/lib/python3.9/dist-packages/pandas/core/indexing.py:1773: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Train data shape=(71882, 4)
Validation data shape=(20537, 4)
Test data shape=(10270, 4)


In [20]:
train_data

K02-CH  week_day  hour  minute
timestamp                                            
2021-11-19 03:55:00 -0.114803       4.0   3.0    55.0
2021-11-19 04:00:00 -0.114803       4.0   4.0     0.0
2021-11-19 04:05:00  0.101132       4.0   4.0     5.0
2021-11-19 04:10:00 -0.114803       4.0   4.0    10.0
2021-11-19 04:15:00 -0.114803       4.0   4.0    15.0
...                       ...       ...   ...     ...
2022-07-27 00:15:00 -0.762608       2.0   0.0    15.0
2022-07-27 00:20:00 -0.762608       2.0   0.0    20.0
2022-07-27 00:25:00 -0.978543       2.0   0.0    25.0
2022-07-27 00:30:00 -0.870575       NaN   NaN     NaN
2022-07-27 00:35:00 -0.762608       2.0   0.0    35.0

[71882 rows x 4 columns]

In [ ]:
def make_dataset(df, window_size=10) -> (np.array, np.array):
  np_data = df.to_numpy()
  inputs = []
  labels = []
  for i in range(len(np_data)-window_size):
    input = [[e] for e in np_data[i:i+window_size]]
    inputs.append(input)
    label = np_data[i+window_size]
    labels.append(label)
  return np.array(inputs), np.array(labels)

In [ ]:
# WINDOW_SIZE=24
# train_inputs, train_labels = make_dataset(train, WINDOW_SIZE)
# val_inputs, val_labels = make_dataset(val, WINDOW_SIZE)
# test_inputs, test_labels = make_dataset(test, WINDOW_SIZE)
# train_inputs.shape, train_labels.shape, val_inputs.shape, val_labels.shape, test_inputs.shape, test_labels.shape

((71917, 24, 1), (71917,), (20530, 24, 1), (20530,), (10255, 24, 1), (10255,))

In [ ]:
from keras.models import Sequential
from keras.layers import InputLayer, LSTM, Dense
from keras.callbacks import ModelCheckpoint
from keras.losses import MeanSquaredError, MeanAbsolutePercentageError
from keras.metrics import RootMeanSquaredError
from keras.optimizers import Adam

model1 = Sequential()
model1.add(InputLayer((WINDOW_SIZE, 1)))
model1.add(LSTM(64, return_sequences=True))
model1.add(LSTM(64))
model1.add(Dense(128, 'relu'))
model1.add(Dense(128, 'relu'))
model1.add(Dense(128, 'relu'))
model1.add(Dense(128, 'relu'))
model1.add(Dense(1, 'linear'))
model1.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_2 (LSTM)               (None, 24, 64)            16896     
                                                                 
 lstm_3 (LSTM)               (None, 64)                33024     
                                                                 
 dense_5 (Dense)             (None, 128)               8320      
                                                                 
 dense_6 (Dense)             (None, 128)               16512     
                                                                 
 dense_7 (Dense)             (None, 128)               16512     
                                                                 
 dense_8 (Dense)             (None, 128)               16512     
                                                                 
 dense_9 (Dense)             (None, 1)                

In [ ]:
checkpoint = ModelCheckpoint('model/v1', save_best_only=True)
model1.compile(loss=MeanSquaredError(), optimizer=Adam(learning_rate=0.0001), metrics=[RootMeanSquaredError()])

In [ ]:
model1.fit(train_inputs, train_labels, validation_data=(val_inputs, val_labels), epochs=10, callbacks=[checkpoint])

Epoch 1/10
2243/2248 [============================>.] - ETA: 0s - loss: 0.1124 - root_mean_squared_error: 0.3353

2248/2248 [==============================] - 28s 12ms/step - loss: 0.1123 - root_mean_squared_error: 0.3351 - val_loss: 0.0913 - val_root_mean_squared_error: 0.3021
Epoch 2/10
2248/2248 [==============================] - 18s 8ms/step - loss: 0.0671 - root_mean_squared_error: 0.2591 - val_loss: 0.0942 - val_root_mean_squared_error: 0.3068
Epoch 3/10
2246/2248 [============================>.] - ETA: 0s - loss: 0.0644 - root_mean_squared_error: 0.2538

2248/2248 [==============================] - 25s 11ms/step - loss: 0.0644 - root_mean_squared_error: 0.2538 - val_loss: 0.0837 - val_root_mean_squared_error: 0.2894
Epoch 4/10
2241/2248 [============================>.] - ETA: 0s - loss: 0.0639 - root_mean_squared_error: 0.2527

2248/2248 [==============================] - 25s 11ms/step - loss: 0.0638 - root_mean_squared_error: 0.2526 - val_loss: 0.0827 - val_root_mean_squared_error: 0.2875
Epoch 5/10
2241/2248 [============================>.] - ETA: 0s - loss: 0.0634 - root_mean_squared_error: 0.2517

2248/2248 [==============================] - 25s 11ms/step - loss: 0.0634 - root_mean_squared_error: 0.2518 - val_loss: 0.0821 - val_root_mean_squared_error: 0.2865
Epoch 6/10
2248/2248 [==============================] - 18s 8ms/step - loss: 0.0630 - root_mean_squared_error: 0.2510 - val_loss: 0.0844 - val_root_mean_squared_error: 0.2906
Epoch 7/10
2245/2248 [============================>.] - ETA: 0s - loss: 0.0628 - root_mean_squared_error: 0.2505

2248/2248 [==============================] - 25s 11ms/step - loss: 0.0628 - root_mean_squared_error: 0.2505 - val_loss: 0.0791 - val_root_mean_squared_error: 0.2813
Epoch 8/10
2248/2248 [==============================] - 18s 8ms/step - loss: 0.0623 - root_mean_squared_error: 0.2497 - val_loss: 0.0914 - val_root_mean_squared_error: 0.3023
Epoch 9/10
2248/2248 [==============================] - 18s 8ms/step - loss: 0.0622 - root_mean_squared_error: 0.2494 - val_loss: 0.0838 - val_root_mean_squared_error: 0.2895
Epoch 10/10
2248/2248 [==============================] - 18s 8ms/step - loss: 0.0619 - root_mean_squared_error: 0.2487 - val_loss: 0.0805 - val_root_mean_squared_error: 0.2837


In [ ]:
from keras.models import load_model
model1 = load_model('model/v1')

In [ ]:
val_predict = model1.predict(val_inputs).flatten()
val_results = pd.DataFrame(data={'Validation Predictions':val_predict, 'Actuals':val_labels})
val_results
# plot([pd.Series(predict), pd.Series(test_labels)], subplot_pos=[0, 0])

642/642 [==============================] - 3s 3ms/step


Validation Predictions   Actuals
0                   -0.852962 -0.719955
1                   -0.769466 -0.963215
2                   -0.903606 -0.963215
3                   -0.928243 -0.882128
4                   -0.897837 -0.801042
...                       ...       ...
20525               -0.723550 -0.476695
20526               -0.420793  0.253084
20527                0.325114  0.982864
20528                0.940008  1.226124
20529                1.270356  1.469384

[20530 rows x 2 columns]

In [ ]:
plot([pd.Series(val_predict), pd.Series(val_labels)], subplot_pos=[0, 0])

In [ ]:
results = model1.evaluate(val_inputs, val_labels)
print(f"test loss={results[0]}, test acc={results[1]}")

642/642 [==============================] - 3s 4ms/step - loss: 0.0791 - root_mean_squared_error: 0.2813
test loss=0.07912041991949081, test acc=0.28128352761268616
